<a href="https://colab.research.google.com/github/MLPA-T3/Big-Data-Analytics/blob/main/glassdoor_review_eda_plotly_threshold_all_companies.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>


# Glassdoor Reviews — Interactive EDA (Thresholded; **All Companies**)

This build keeps `TOP_N = 20` for **non-company** groupings, but shows **ALL companies** (subject to `MIN_COUNT`) for:
- Avg Overall Rating by Company
- Avg Overall Theme Sentiment by Company
- Company–Theme Heatmap
- Company Bubble (sentiment vs overall)
- Radar (rating profile by company)
- Treemap (Company → City)

It is NA-safe and uses the same robust helpers as before.


## 1) Setup & Deps

In [1]:

# In Colab you can leave these; locally you may comment out.
!pip -q install plotly kaleido openpyxl


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 51.5/51.5 kB 3.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 51.3/51.3 kB 2.7 MB/s eta 0:00:00


## 2) Parameters

In [2]:

import io, os, re, warnings
import numpy as np
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go

warnings.filterwarnings("ignore")

# --- Global controls ---
MIN_COUNT = 25     # minimum reviews per group to include
TOP_N = 20         # default top-N for non-company charts
TOP_N_COMPANIES = None  # None → include ALL companies (meeting MIN_COUNT)
EXPORT_STATIC = False
EXPORT_DIR = "figures"
if EXPORT_STATIC and not os.path.exists(EXPORT_DIR):
    os.makedirs(EXPORT_DIR, exist_ok=True)

print("MIN_COUNT =", MIN_COUNT, "| TOP_N (non-company) =", TOP_N, "| TOP_N_COMPANIES =", TOP_N_COMPANIES)


MIN_COUNT = 25 | TOP_N (non-company) = 20 | TOP_N_COMPANIES = None


## 3) Data Load

In [3]:

# Option A: point to your path (e.g., in Drive after mounting)
DATA_PATH = None  # '/content/drive/MyDrive/Review-results.xlsx'

def try_read_excel(path):
    try:
        return pd.read_excel(path)
    except Exception:
        return None

reviews = None
if DATA_PATH:
    reviews = try_read_excel(DATA_PATH)

if reviews is None:
    # Colab upload path
    try:
        from google.colab import files
        uploaded = files.upload()
        if uploaded:
            up = list(uploaded.keys())[0]
            reviews = pd.read_excel(io.BytesIO(uploaded[up]))
    except Exception:
        pass

# Local fallback for this environment
if reviews is None:
    reviews = pd.read_excel('/mnt/data/Review-results.xlsx')

print("Loaded shape:", reviews.shape)
reviews.head(3)


Saving Review-results.xlsx to Review-results.xlsx
Loaded shape: (6430, 38)


ReviewID   advice                                               pros  \
0  99550437      NaN                            best place to work ever   
1  99307007  nothing                    good working culture and growth   
2  99280869      NaN  Transparent communication from leadership duri...   

                                                cons  \
0                             no cons till yet found   
1          need more employee facilities such as gym   
2  Workload can be high during product release cy...   

                                             summary  countHelpful  \
0                                   best environment             0   
1                                    over all review             0   
2  Great place for skill-building, but work-life ...             0   

   employer/id        employer/name  isCurrentJob              jobTitle/text  \
0        32171  3i Infotech Limited          True   Senior Software Engineer   
1        32171  3i Infotech Limited         False  Assistant General Manager   
2        32171  3i Infotech Limited         False       IT Security Engineer   

   ...  theme::Leadership & Management  theme::Autonomy and Job Content  \
0  ...                        0.359390                         0.678548   
1  ...                        0.244442                         0.561398   
2  ...                        0.778461                         0.796493   

  theme::Teamwork share::Career Growth  share::Compensation & Benefits  \
0        0.485434             0.081817                        0.092190   
1        0.416983             0.085509                        0.067306   
2        0.802147             0.390807                        0.069028   

  share::Work-Life Balance  share::Culture & Values  \
0                 0.261684                 0.147206   
1                 0.146022                 0.245196   
2                 0.165890                 0.074204   

   share::Leadership & Management  share::Autonomy and Job Content  \
0                        0.114212                         0.095208   
1                        0.180876                         0.082806   
2                        0.131183                         0.062471   

   share::Teamwork  
0         0.207683  
1         0.192285  
2         0.106417  

[3 rows x 38 columns]

## 4) Cleaning & Derived

In [19]:

# 4.1 Normalize column names
reviews.columns = [c.strip() for c in reviews.columns]

# 4.2 Column matcher
def match_col(df, *candidates):
    low = {c.lower().strip(): c for c in df.columns}
    for cand in candidates:
        key = cand.lower().strip()
        if key in low:
            return low[key]
    for c in df.columns:
        if any(cand.lower().strip() in c.lower() for cand in candidates):
            return c
    raise KeyError(f"Could not find any of: {candidates}")

col_company = match_col(reviews, "employer/name", "company", "employer")
col_city    = match_col(reviews, "location/name", "city", "location")
col_title   = match_col(reviews, "jobTitle/text", "job_title", "title")
col_status  = match_col(reviews, "isCurrentJob", "is_current_job", "is_current")
col_overall = match_col(reviews, "ratingOverall", "overall_rating", "overall")

# 4.3 Ratings
rating_candidates = [
    "ratingCareerOpportunities","ratingCompensationAndBenefits",
    "ratingCultureAndValues","ratingDiversityAndInclusion",
    "ratingSeniorLeadership","ratingWorkLifeBalance",
]
rating_cols = []
for rc in rating_candidates:
    try:
        rating_cols.append(match_col(reviews, rc))
    except KeyError:
        pass
if col_overall not in rating_cols:
    rating_cols.append(col_overall)
for c in rating_cols:
    reviews[c] = pd.to_numeric(reviews[c], errors="coerce")

# 4.4 Themes (shares + polarity under theme::*)
share_cols = [c for c in reviews.columns if c.lower().startswith("share::")]
pol_cols   = [c for c in reviews.columns if c.lower().startswith("polarity::")]
if not pol_cols:
    pol_cols = [c for c in reviews.columns if c.lower().startswith("theme::")]

def tname(col):
    return col.split("::", 1)[1] if "::" in col else col

themes = sorted(set(map(tname, share_cols)).intersection(map(tname, pol_cols)))

# 4.5 Share-weighted overall theme sentiment
if themes:
    parts = []
    for th in themes:
        s = next(c for c in share_cols if tname(c)==th)
        p = next(c for c in pol_cols  if tname(c)==th)
        parts.append(reviews[s].astype(float) * reviews[p].astype(float))
    numerator   = pd.concat(parts, axis=1).sum(axis=1)
    denominator = reviews[share_cols].astype(float).sum(axis=1).replace(0, np.nan)
    reviews["overall_theme_sentiment"] = numerator / denominator
else:
    reviews["overall_theme_sentiment"] = np.nan

# 4.6 Tenure parsing → bins (if present)
def parse_tenure_to_years(x):
    if pd.isna(x): return np.nan
    if isinstance(x,(int,float)): return x/12.0 if x>50 else float(x)
    s = str(x).lower().strip()
    nums = re.findall(r"[\d\.]+", s)
    if not nums: return np.nan
    val = float(nums[0])
    return val/12.0 if "month" in s else val

if "lengthOfEmployment" in reviews.columns:
    reviews["tenure_years"] = reviews["lengthOfEmployment"].apply(parse_tenure_to_years)
    bins   = [-0.01, 0.5, 1.5, 3, 5, 10, 100]
    labels = ["<6 mo","6–18 mo","1.5–3y","3–5y","5–10y","10y+"]
    reviews["tenure_bin"] = pd.cut(reviews["tenure_years"], bins=bins, labels=labels)

# 4.7 Standardize status
reviews[col_status] = reviews[col_status].map({True:"Current", False:"Former", 1:"Current", 0:"Former"}).fillna(reviews[col_status].astype(str))

# 4.8 Clean label columns to avoid pd.NA in Plotly
for c in [col_company, col_city, col_title]:
    reviews[c] = (reviews[c]
                  .astype("string")
                  .fillna("Unknown")
                  .str.strip()
                  .replace("", "Unknown")
                  .replace("<NA>", "Unknown")
                  .astype(str))

print("Themes detected:", len(themes))


Themes detected: 7


## 5) Helpers

In [20]:

def vc_to_frame(series, label="Label", count_name="Count", n=20):
    df = (
        series.astype("string").fillna("Unknown").replace("<NA>","Unknown")
        .value_counts(dropna=False)
        .rename_axis(label).reset_index(name=count_name)
        .sort_values(count_name, ascending=False)
        .head(n)
    )
    df[label] = df[label].astype(str)
    df[count_name] = df[count_name].astype(int)
    return df

def mean_with_count(df, group_col, value_col, min_n=0, top_n=None, label=None):
    """NA-safe mean + count, with optional top_n (None = all)."""
    if label is None: label = group_col
    agg = df.groupby(group_col, dropna=False)[value_col].agg(['mean','size']).reset_index()
    agg.columns = [label, 'mean_val', 'N']
    agg[label] = agg[label].astype("string").fillna("Unknown").replace("<NA>","Unknown").astype(str)
    agg['mean_val'] = pd.to_numeric(agg['mean_val'], errors='coerce').astype(float)
    agg['N'] = pd.to_numeric(agg['N'], errors='coerce').fillna(0).astype(int)
    agg = agg[(agg['N'] >= min_n) & agg['mean_val'].notna()]
    agg = agg.sort_values('mean_val', ascending=False)
    if isinstance(top_n, int) and top_n>0:
        agg = agg.head(top_n)
    agg.columns = [label, f"Mean {value_col}", "N"]
    return agg

_def_export = lambda fig, name: fig.write_image(f"{EXPORT_DIR}/{name}.png", scale=2) if EXPORT_STATIC else None


## 6) Top-N counts (non-company)

In [21]:

fig = px.bar(vc_to_frame(reviews[col_city], "City", n=TOP_N), x="City", y="Count",
             title=f"Top {TOP_N} Cities by Review Count")
fig.update_layout(xaxis_tickangle=-45); _def_export(fig, "top_cities_counts"); fig.show()

fig = px.bar(vc_to_frame(reviews[col_title], "Job Title", n=TOP_N), x="Job Title", y="Count",
             title=f"Top {TOP_N} Job Titles by Review Count")
fig.update_layout(xaxis_tickangle=-45); _def_export(fig, "top_titles_counts"); fig.show()


## 7) Ratings — distribution & means (All companies; Top 20 elsewhere)

In [22]:

# Distribution
fig = px.histogram(reviews, x=col_overall, nbins=20, title="Distribution of Overall Rating")
fig.update_layout(xaxis_title="Overall", yaxis_title="Count"); _def_export(fig, "dist_overall"); fig.show()

# Company means: ALL companies (N ≥ MIN_COUNT)
comp_mean_overall = mean_with_count(reviews, col_company, col_overall, min_n=MIN_COUNT, top_n=TOP_N_COMPANIES, label="Company")
fig = px.bar(comp_mean_overall, x="Company", y=f"Mean {col_overall}", hover_data=["N"],
             title=f"Avg Overall Rating by Company (All, N≥{MIN_COUNT})")
fig.update_layout(xaxis_tickangle=-45, yaxis_title="Mean Overall")
_def_export(fig, "mean_overall_by_company_all"); fig.show()

# City / Title means: Top 20
city_mean_overall  = mean_with_count(reviews, col_city,  col_overall, min_n=MIN_COUNT, top_n=TOP_N, label="City")
fig = px.bar(city_mean_overall, x="City", y=f"Mean {col_overall}", hover_data=["N"],
             title=f"Avg Overall Rating by City (Top {TOP_N}, N≥{MIN_COUNT})")
fig.update_layout(xaxis_tickangle=-45, yaxis_title="Mean Overall")
_def_export(fig, "mean_overall_by_city_top20"); fig.show()

title_mean_overall = mean_with_count(reviews, col_title, col_overall, min_n=MIN_COUNT, top_n=TOP_N, label="Job Title")
fig = px.bar(title_mean_overall, x="Job Title", y=f"Mean {col_overall}", hover_data=["N"],
             title=f"Avg Overall Rating by Job Title (Top {TOP_N}, N≥{MIN_COUNT})")
fig.update_layout(xaxis_tickangle=-45, yaxis_title="Mean Overall")
_def_export(fig, "mean_overall_by_title_top20"); fig.show()


## 8) Employment Status (per-review)

In [23]:

fig = px.box(reviews, x=col_status, y=col_overall, points="all", title="Overall Rating by Employment Status")
_def_export(fig, "overall_by_status"); fig.show()

fig = px.violin(reviews, x=col_status, y="overall_theme_sentiment", box=True, points="all",
                title="Overall Theme Sentiment by Employment Status")
_def_export(fig, "sentiment_by_status"); fig.show()


## 9) Tenure bins (per-review)

In [24]:

if "tenure_bin" in reviews.columns:
    fig = px.box(reviews, x="tenure_bin", y=col_overall, points="outliers",
                 title="Overall Rating by Tenure Bin")
    _def_export(fig, "overall_by_tenure"); fig.show()

    fig = px.box(reviews, x="tenure_bin", y="overall_theme_sentiment", points="outliers",
                 title="Overall Theme Sentiment by Tenure Bin")
    _def_export(fig, "sentiment_by_tenure"); fig.show()


## 10) Overall Theme Sentiment — distribution & means (All companies; Top 20 elsewhere)

In [25]:

fig = px.histogram(reviews, x="overall_theme_sentiment", nbins=30,
                   title="Distribution of Overall Theme Sentiment (share-weighted)")
fig.update_layout(xaxis_title="Sentiment", yaxis_title="Count"); _def_export(fig, "dist_sentiment"); fig.show()

# Company means: ALL companies (N ≥ MIN_COUNT)
comp_mean_sent = mean_with_count(reviews, col_company, "overall_theme_sentiment", min_n=MIN_COUNT, top_n=TOP_N_COMPANIES, label="Company")
fig = px.bar(comp_mean_sent, x="Company", y="Mean overall_theme_sentiment", hover_data=["N"],
             title=f"Avg Overall Theme Sentiment by Company (All, N≥{MIN_COUNT})")
fig.update_layout(xaxis_tickangle=-45, yaxis_title="Mean Sentiment")
_def_export(fig, "mean_sent_by_company_all"); fig.show()

# City / Title means: Top 20
city_mean_sent = mean_with_count(reviews, col_city, "overall_theme_sentiment", min_n=MIN_COUNT, top_n=TOP_N, label="City")
fig = px.bar(city_mean_sent, x="City", y="Mean overall_theme_sentiment", hover_data=["N"],
             title=f"Avg Overall Theme Sentiment by City (Top {TOP_N}, N≥{MIN_COUNT})")
fig.update_layout(xaxis_tickangle=-45, yaxis_title="Mean Sentiment")
_def_export(fig, "mean_sent_by_city_top20"); fig.show()

title_mean_sent = mean_with_count(reviews, col_title, "overall_theme_sentiment", min_n=MIN_COUNT, top_n=TOP_N, label="Job Title")
fig = px.bar(title_mean_sent, x="Job Title", y="Mean overall_theme_sentiment", hover_data=["N"],
             title=f"Avg Overall Theme Sentiment by Job Title (Top {TOP_N}, N≥{MIN_COUNT})")
fig.update_layout(xaxis_tickangle=-45, yaxis_title="Mean Sentiment")
_def_export(fig, "mean_sent_by_title_top20"); fig.show()


## 11) Sentiment vs Ratings (per-review)

In [26]:

for rc in ['ratingCareerOpportunities','ratingCeo','ratingCompensationAndBenefits','ratingCultureAndValues','ratingDiversityAndInclusion','ratingSeniorLeadership','ratingWorkLifeBalance','ratingOverall']:
    if rc in reviews.columns:
        fig = px.scatter(reviews, x="overall_theme_sentiment", y=rc, trendline="ols",
                         title=f"{rc} vs Overall Theme Sentiment")
        _def_export(fig, f"{rc}_vs_sentiment"); fig.show()


## 12) Company–Theme Share Heatmap — **All companies** (N≥MIN_COUNT)

In [27]:

share_cols = [c for c in reviews.columns if c.lower().startswith("share::")]
if len(share_cols) > 0:
    def tname(col):
        return col.split("::", 1)[1] if "::" in col else col
    theme_names = sorted(set(map(tname, share_cols)))

    counts = reviews.groupby(col_company).size().rename("N").reset_index()
    counts["N"] = counts["N"].astype(int)
    keep_companies = counts[counts["N"] >= MIN_COUNT][col_company]
    sub = reviews[reviews[col_company].isin(keep_companies)].copy()

    # ALL companies (no top-N cut)
    company_order = sub.groupby(col_company).size().sort_values(ascending=False).index.tolist()

    # Build matrix
    data = {}
    for th in theme_names:
        s_col = next(c for c in share_cols if tname(c)==th)
        data[th] = sub.groupby(col_company)[s_col].mean()
    heat_df = pd.DataFrame(data).reindex(index=company_order)

    fig = px.imshow(heat_df, aspect="auto", title=f"Company–Theme Share Heatmap (mean share) — All companies (N≥{MIN_COUNT})")
    _def_export(fig, "company_theme_heatmap_all"); fig.show()


## 13) Treemap — Company → City (All companies, N≥MIN_COUNT)

In [28]:

leaf = (reviews[[col_company, col_city]]
          .astype({col_company: "string", col_city: "string"})
          .fillna({col_company: "Unknown Company", col_city: "Unknown City"}))
leaf[col_company] = leaf[col_company].str.strip().replace(["","<NA>"], "Unknown Company").astype(str)
leaf[col_city]    = leaf[col_city].str.strip().replace(["","<NA>"], "Unknown City").astype(str)

leaf = leaf.groupby([col_company, col_city], dropna=False).size().rename("Reviews").reset_index()
leaf["Reviews"] = leaf["Reviews"].astype(int)

comp_counts = leaf.groupby(col_company)["Reviews"].sum().rename("N").reset_index()
comp_counts["N"] = comp_counts["N"].astype(int)
keep_companies = comp_counts[comp_counts["N"] >= MIN_COUNT][col_company]
leaf = leaf[leaf[col_company].isin(keep_companies)]

# No top cut → ALL kept companies
fig = px.treemap(leaf, path=[col_company, col_city], values="Reviews",
                 title=f"Review Counts: Company → City (All companies, N≥{MIN_COUNT})")
fig.update_traces(root_color="lightgrey")
fig.update_layout(margin=dict(t=50, l=0, r=0, b=0))
_def_export(fig, "treemap_company_city_all"); fig.show()


## 14) Bubble — Sentiment vs Overall (All companies, N≥MIN_COUNT)

In [29]:

grp = reviews.groupby(col_company).agg(
    avg_sent=("overall_theme_sentiment","mean"),
    avg_overall=(col_overall,"mean"),
    n=(col_overall,"size")
).reset_index()
grp["n"] = grp["n"].astype(int)
grp = grp[grp["n"] >= MIN_COUNT].sort_values("n", ascending=False)
grp[col_company] = grp[col_company].astype("string").fillna("Unknown").replace("<NA>","Unknown").astype(str)

fig = px.scatter(grp, x="avg_sent", y="avg_overall", size="n", hover_name=col_company,
                 title=f"Company Bubble: Sentiment vs Overall — All companies (N≥{MIN_COUNT})",
                 size_max=50)
_def_export(fig, "company_bubble_all"); fig.show()


## 15) Radar — Rating profile by company (All companies, N≥MIN_COUNT)

In [30]:

rcols = [c for c in rating_cols if c != col_overall]
if len(rcols) >= 3:
    counts = reviews.groupby(col_company).size().rename("N").reset_index()
    counts["N"] = counts["N"].astype(int)
    keep = counts[counts["N"] >= MIN_COUNT][col_company]
    company_list = (reviews[reviews[col_company].isin(keep)]
                    .groupby(col_company).size().sort_values(ascending=False).index.tolist())
    if len(company_list) > 0:
        traces, buttons = [], []
        for i, comp in enumerate(company_list):
            sub = reviews[reviews[col_company]==comp][rcols].mean()
            traces.append(go.Scatterpolar(r=sub.values, theta=rcols, fill='toself', name=comp, visible=(i==0)))
            buttons.append(dict(label=comp, method="update",
                                args=[{"visible":[j==i for j in range(len(company_list))]},
                                      {"title": f"Rating Profile — {comp} (N≥{MIN_COUNT})"}]))
        fig = go.Figure(data=traces)
        fig.update_layout(title=f"Rating Profile — {company_list[0]} (N≥{MIN_COUNT})",
                          polar=dict(radialaxis=dict(visible=True, range=[0,5])),
                          updatemenus=[dict(type="dropdown", x=1.15, y=1, showactive=True, buttons=buttons)])
        _def_export(fig, "radar_rating_profile_all"); fig.show()


## 16) Scatter Matrix & Correlation (per-review)

In [31]:

num_cols = [c for c in rating_cols]
if "overall_theme_sentiment" in reviews.columns:
    num_cols = list(dict.fromkeys(num_cols + ["overall_theme_sentiment"]))

if len(num_cols) >= 2:
    fig = px.scatter_matrix(reviews[num_cols], title="Scatter Matrix: Ratings + Sentiment")
    _def_export(fig, "scatter_matrix"); fig.show()

    corr = reviews[num_cols].astype(float).corr()
    fig = px.imshow(corr, text_auto=True, aspect="auto", title="Correlation Heatmap")
    _def_export(fig, "correlation_heatmap"); fig.show()


## 17) Outlier Companies — rating vs sentiment discrepancy (All companies, N≥MIN_COUNT)

In [32]:

grp = reviews.groupby(col_company).agg(
    avg_sent=("overall_theme_sentiment","mean"),
    avg_overall=(col_overall,"mean"),
    n=("overall_theme_sentiment","size")
).dropna()
grp["n"] = grp["n"].astype(int)
grp = grp[grp["n"] >= MIN_COUNT]
s1 = (grp["avg_sent"] - grp["avg_sent"].mean()) / grp["avg_sent"].std(ddof=0)
s2 = (grp["avg_overall"] - grp["avg_overall"].mean()) / grp["avg_overall"].std(ddof=0)
grp["delta_rating_minus_sentiment"] = s2 - s1
outliers = grp.sort_values("delta_rating_minus_sentiment", ascending=False).reset_index()
outliers


employer/name  avg_sent  avg_overall    n  \
0                 Honeywell International Inc.  0.254163     3.906250  192   
1                              Infosys Limited  0.237261     3.792929  198   
2                      ITC Infotech India Ltd.  0.313502     4.117347  196   
3                  TCS Thomas Computer Service  0.186469     3.489796  196   
4                                  Google Inc.  0.416927     4.465969  191   
5   Cognizant Technology Solutions Corporation  0.194664     3.510101  198   
6                                       Cyient  0.226741     3.570707  198   
7                 Advanced Micro Devices, Inc.  0.322213     3.968421  190   
8                        Tech Mahindra Limited  0.208276     3.474747  198   
9                        Microsoft Corporation  0.287466     3.812500  192   
10                               Collabera LLC  0.341660     3.978836  189   
11                          Oracle Corporation  0.233978     3.510870  184   
12                   Tally Solutions Pvt. Ltd.  0.414819     4.280612  196   
13                             Mphasis Limited  0.224667     3.444444  198   
14                  Hewlett Packard Enterprise  0.368249     4.035897  195   
15                   Zoho Corporation Pvt. Ltd  0.391006     4.130208  192   
16   Sasken Communication Technologies Limited  0.295718     3.722222  198   
17                       HCL Technologies Ltd.  0.217032     3.384615  195   
18           Birlasoft (India) Private Limited  0.235319     3.461929  197   
19                         WNS Global Services  0.171511     3.177665  197   
20                      KPIT Technologies Ltd.  0.202973     3.306122  196   
21                         LTIMindtree Limited  0.243504     3.479592  196   
22                              Autodesk, Inc.  0.327419     3.791667  192   
23                             Godrej Infotech  0.334932     3.803030  198   
24                        LinkedIn Corporation  0.365731     3.915344  189   
25                          Dassault SystÃ¨mes  0.358567     3.875648  193   
26                     L&T Technology Services  0.208526     3.221106  199   
27                 Zensar Technologies Limited  0.310265     3.651515  198   
28            Hinduja Global Solutions Limited  0.187179     3.123711  194   
29                         3i Infotech Limited  0.222002     3.241026  195   
30                     Persistent Systems Ltd.  0.360162     3.793970  199   
31                   NIIT Technologies Limited  0.226223     3.166667  198   
32                                  Salesforce  0.482920     4.088083  193   

    delta_rating_minus_sentiment  
0                       1.020309  
1                       0.899562  
2                       0.893954  
3                       0.646949  
4                       0.616822  
5                       0.603424  
6                       0.377468  
7                       0.345287  
8                       0.327599  
9                       0.324076  
10                      0.130712  
11                      0.109884  
12                      0.097250  
13                      0.031597  
14                     -0.036479  
15                     -0.045587  
16                     -0.045994  
17                     -0.048409  
18                     -0.051226  
19                     -0.084093  
20                     -0.102381  
21                     -0.102409  
22                     -0.241168  
23                     -0.302435  
24                     -0.359932  
25                     -0.386541  
26                     -0.422912  
27                     -0.437785  
28                     -0.440665  
29                     -0.534167  
30                     -0.647329  
31                     -0.806499  
32                     -1.328883

## 18) Export toggle

In [18]:

print("EXPORT_STATIC =", EXPORT_STATIC, "| Directory:", EXPORT_DIR)
print("If True, re-run cells above to write PNGs into the folder.")


EXPORT_STATIC = False | Directory: figures
If True, re-run cells above to write PNGs into the folder.
